# Derma-Challenge

Para  comenzar, importaremos las bibliotecas necesarias

In [2]:
import os
import random
import numpy as np
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torchvision.transforms.functional as TF

from torch.utils.data import Dataset, DataLoader
from PIL import Image

## Dataset Processing

Deleting empty classes and organizing dataset for usage

In [24]:
import os
import random
import shutil

# Define paths
input_folder = 'images/images'
output_folder = 'data/'

# Create the output folder structure
os.makedirs(output_folder, exist_ok=True)
os.makedirs(os.path.join(output_folder, 'train'), exist_ok=True)
os.makedirs(os.path.join(output_folder, 'val'), exist_ok=True)
os.makedirs(os.path.join(output_folder, 'test'), exist_ok=True)

# Function to create class folders
def create_class_folders(folder_path):
    for class_name in os.listdir(input_folder):
        os.makedirs(os.path.join(folder_path, class_name), exist_ok=True)

# Count images per class
class_images = {}
for class_name in os.listdir(input_folder):
    class_images[class_name] = len([f for f in os.listdir(os.path.join(input_folder, class_name)) if f.endswith('.png')])
    print(f"Class {class_name}: {class_images[class_name]} images")

# Calculate number of images for each split per class
class_splits = {}
for class_name, count in class_images.items():
    if count < 3:
        print(f"Not enough images for class {class_name}. Skipping this class.")
        continue
    
    class_splits[class_name] = {
        'train': min(int(count * 0.8), count),
        'val': min(int(count * 0.1), count),
    }
    class_splits[class_name]['test'] = max(0, count - class_splits[class_name]['train'] - class_splits[class_name]['val'])

# Split images into train, val, and test sets for each class
class_file_lists = {}
for class_name in class_images.keys():
    if class_name not in class_splits:
        continue
    
    class_files = []
    for filename in os.listdir(os.path.join(input_folder, class_name)):
        if filename.endswith('.png'):
            class_files.append(filename)
    
    random.shuffle(class_files)
    
    train_files = class_files[:class_splits[class_name]['train']]
    val_files = class_files[class_splits[class_name]['train']:class_splits[class_name]['train']+class_splits[class_name]['val']]
    test_files = class_files[class_splits[class_name]['train']+class_splits[class_name]['val']:]
    
    class_file_lists[class_name] = {'train': train_files, 'val': val_files, 'test': test_files}

# Copy images to the appropriate folders
for class_name, file_list in class_file_lists.items():
    if not file_list['train'] or not file_list['val'] or not file_list['test']:
        print(f"Not enough images for class {class_name}. Skipping this class.")
        continue
    
    for split, files in [('train', file_list['train']), ('val', file_list['val']), ('test', file_list['test'])]:
        for filename in files:
            src_path = os.path.join(input_folder, class_name, filename)
            dst_folder = os.path.join(output_folder, split)
            dst_path = os.path.join(output_folder, split, class_name, filename)
            create_class_folders(dst_folder)
            shutil.copy2(src_path, dst_path)
            print(f"Copied {src_path} to {dst_path}")

print("\nData copying completed.")

Class acrochordon: 301 images
Class actinic_keratosis: 1350 images
Class aimp: 0 images
Class angiofibroma_or_fibrous_papule: 4 images
Class angiokeratoma: 13 images
Class angioma: 71 images
Class atypical_spitz_tumor: 5 images
Class basal_cell_carcinoma: 4767 images
Class cafe_au_lait_macule: 0 images
Class clear_cell_acanthoma: 6 images
Class dermatofibroma: 398 images
Class lentigo_nos: 0 images
Class lentigo_simplex: 43 images
Class lichenoid_keratosis: 311 images
Class melanoma: 7226 images
Class melanoma_metastasis: 39 images
Class missing_key: 0 images
Class neurofibroma: 26 images
Class nevus: 32608 images
Class nevus_spilus: 1 images
Class other: 33 images
Class pigmented_benign_keratosis: 1339 images
Class pyogenic_granuloma: 3 images
Class scar: 29 images
Class sebaceous_adenoma: 2 images
Class sebaceous_hyperplasia: 7 images
Class seborrheic_keratosis: 1905 images
Class solar_lentigo: 558 images
Class squamous_cell_carcinoma: 1301 images
Class vascular_lesion: 338 images
Cl

In [25]:
import os

# Checking if dataset is correctly splitted

train_folder = 'data/train/'
eval_folder = 'data/test/'
validation_folder = 'data/val/'
input_folder = 'images/images'
for class_name in os.listdir(input_folder):
    train_images = len([f for f in os.listdir(os.path.join(train_folder, class_name)) if f.endswith('.png')])
    eval_images = len([f for f in os.listdir(os.path.join(eval_folder, class_name)) if f.endswith('.png')])
    validation_images = len([f for f in os.listdir(os.path.join(validation_folder, class_name)) if f.endswith('.png')])
    total_images = len([f for f in os.listdir(os.path.join(input_folder, class_name))if f.endswith('.png')])
    print(f'class: {class_name}; train {train_images}; eval {eval_images}; val {validation_images}; total {total_images}')


class: acrochordon; train 240; eval 31; val 30; total 301
class: actinic_keratosis; train 1080; eval 135; val 135; total 1350
class: aimp; train 0; eval 0; val 0; total 0
class: angiofibroma_or_fibrous_papule; train 0; eval 0; val 0; total 4
class: angiokeratoma; train 10; eval 2; val 1; total 13
class: angioma; train 56; eval 8; val 7; total 71
class: atypical_spitz_tumor; train 0; eval 0; val 0; total 5
class: basal_cell_carcinoma; train 3813; eval 478; val 476; total 4767
class: cafe_au_lait_macule; train 0; eval 0; val 0; total 0
class: clear_cell_acanthoma; train 0; eval 0; val 0; total 6
class: dermatofibroma; train 318; eval 41; val 39; total 398
class: lentigo_nos; train 0; eval 0; val 0; total 0
class: lentigo_simplex; train 34; eval 5; val 4; total 43
class: lichenoid_keratosis; train 248; eval 32; val 31; total 311
class: melanoma; train 5780; eval 724; val 722; total 7226
class: melanoma_metastasis; train 31; eval 5; val 3; total 39
class: missing_key; train 0; eval 0; val 

Dividing Data into train, test and validation